In [4]:
#Doppler Method for Localizing a receiver
#Fausto Vega

using SatelliteDynamics
using LinearAlgebra
using PlotlyJS
using DelimitedFiles
using Distributions

In [5]:
# Declare simulation initial Epoch. Start time
epc0 = Epoch(2019, 1, 1, 12, 0, 0, 0.0)  #year, month, day, hour, minute, seconds, nanoseconds 

Epoch(2019-01-01T11:59:23.000Z)

In [6]:
# Declare initial state in terms of osculating orbital elements
#semi-major axis, eccentricity, inclination, RAAN, Argument of perigee, Mean anomaly

#1 and 2 on the same orbit, different initial mean anomaly

#original config, working
# iss1 = [7378e3, 0.0004879, 90.6391, 189.0859, 151.2014, 185]; #converges at 189.0859
# iss2 = [7378e3, 0.0004879, 90.6391, 189.0859, 151.2014, 205];
# iss3 = [7378e3, 0.0004879, 90.6391, 201.0859, 151.2014, 190]; # converges a t 200.0859
# iss4 = [7378e3, 0.0004879, 90.6391, 201.0859, 151.2014, 210]; # converges a t 200.0859

#Realistic Orbit
# iss1 = [6871e3, 0.0004879, 90.6391, 194.5859, 151.2014, 190]; 
# iss2 = [6871e3, 0.0004879, 90.6391, 194.5859, 151.2014, 200];
# iss3 = [6871e3, 0.0004879, 90.6391, 195.5859, 151.2014, 193]; 
# iss4 = [6871e3, 0.0004879, 90.6391, 195.5859, 151.2014, 203]; 

#ARGOS Orbit ~850 km altitude

iss1 = [7221e3, 0.0004879, 90.6391, 194.5859, 151.2014, 190]; 
iss2 = [7221e3, 0.0004879, 90.6391, 194.5859, 151.2014, 200];
iss3 = [7221e3, 0.0004879, 90.6391, 195.5859, 151.2014, 193]; 
iss4 = [7221e3, 0.0004879, 90.6391, 195.5859, 151.2014, 203]; 


#Function to convert mean anomoaly to eccentric anomaly
E1 = anomaly_mean_to_eccentric(iss1[6], iss1[2], use_degrees=true); 
E2 = anomaly_mean_to_eccentric(iss2[6], iss2[2], use_degrees=true);
E3 = anomaly_mean_to_eccentric(iss3[6], iss3[2], use_degrees=true);
E4 = anomaly_mean_to_eccentric(iss4[6], iss4[2], use_degrees=true);

In [7]:
# Convert osculating elements to Cartesean state
# returns position and velocity (m, m/s)

eci0_1 = sOSCtoCART(iss1, use_degrees=true)
eci0_2 = sOSCtoCART(iss2, use_degrees=true)
eci0_3 = sOSCtoCART(iss3, use_degrees=true)
eci0_4 = sOSCtoCART(iss4, use_degrees=true)

6-element Vector{Float64}:
      -6.920528693041507e6
      -1.9388943140103715e6
 -732572.827379684
    -746.2067396656779
    -122.5914937915185
    7387.743541399651

In [8]:
#compute the satellite orbital period given the semi-major axis

#same for all 4 satellites since they have the same semi-major axis
T = orbit_period(iss1[1])

#final time for one orbit. Adds initial time to the orbital period

epcf = epc0 + T

Epoch(2019-01-01T13:41:09.705Z)

In [9]:
# Create an EarthInertialState orbit propagagator
#needs initial epoch of state and the state vector
orb1  = EarthInertialState(epc0, eci0_1, dt=1.0,
            mass=1.0, n_grav=0, m_grav=0,
            drag=false, srp=false,
            moon=false, sun=false,
            relativity=false
)

orb2  = EarthInertialState(epc0, eci0_2, dt=1.0,
            mass=1.0, n_grav=0, m_grav=0,
            drag=false, srp=false,
            moon=false, sun=false,
            relativity=false
)

orb3  = EarthInertialState(epc0, eci0_3, dt=1.0,
            mass=1.0, n_grav=0, m_grav=0,
            drag=false, srp=false,
            moon=false, sun=false,
            relativity=false
)

orb4  = EarthInertialState(epc0, eci0_4, dt=1.0,
            mass=1.0, n_grav=0, m_grav=0,
            drag=false, srp=false,
            moon=false, sun=false,
            relativity=false
)

# Propagate the orbit
# orbit until the final time

t_1, epc_1, eci_1 = sim!(orb1, epcf);
t_2, epc_2, eci_2 = sim!(orb2, epcf);
t_3, epc_3, eci_3 = sim!(orb3, epcf);
t_4, epc_4, eci_4 = sim!(orb4, epcf);

In [10]:
#equator position in cartesian coordinates
tag =[-6.128804e6, -1.590206e6, 776.1502e3]

#Examples of putting latitude and longitude and converting to ECEF coordinate frame
#Equitorial position
#tag_geof = [-165.4545, 16.98849, 0]

#North pole position
#tag_geof = [-165.4545, 46.98849, 0]

#tag = sGEOCtoECEF(tag_geof, use_degrees = true)

3-element Vector{Float64}:
     -6.128804e6
     -1.590206e6
 776150.2

In [11]:
#Equitorial Position
#In m
x0= tag[1] 
y0 = tag[2]
z0 = tag[3]

#λ0 = C_LIGHT/400e6 #nominal wavelength in m

f0 = 1e6

#r0 = [x0, y0, z0, λ0]
r0_plot = [x0, y0, z0, f0]

centroid_guess = [(eci_1[1,1]+eci_2[1,1]+eci_3[1,1]+eci_4[1,1])/4, (eci_1[2,1]+eci_2[2,1]+eci_3[2,1]+eci_4[2,1])/4, (eci_1[3,1]+eci_2[3,1]+eci_3[3,1]+eci_4[3,1])/4] 
onearth = sECEFtoGEOC(centroid_guess, use_degrees = true)
geodetic = [onearth[1], onearth[2], 0]

#Guess
xyz = sGEOCtoECEF(geodetic, use_degrees = true)

println(xyz)

[-6.012592823500298e6, -1.636770880711428e6, -1.3602721101371013e6]


In [12]:
#Plot Satellite 1 and 2 Orbit
sat1 = scatter(x=eci_1[1,:], y=eci_1[2,:], z=eci_1[3,:], type="scatter3d", mode="lines", name="orbit 1&2")

#Plot Satellite 3 and 4 Orbit
sat3 = scatter(x=eci_3[1,:], y=eci_3[2,:], z=eci_3[3,:], type="scatter3d", mode="lines", name="orbit 3&4")

#Plot all 4 satellite initial positions
satellites = scatter(x=[eci_1[1,1],eci_2[1,1], eci_3[1,1], eci_4[1,1]], y=[eci_1[2,1],eci_2[2,1], eci_3[2,1], eci_4[2,1]],z=[eci_1[3,1],eci_2[3,1], eci_3[3,1], eci_4[3,1]], mode="markers", marker_size = 4, type="scatter3d", name="satellites")

#Plot Tag position
tag = scatter(x = [r0_plot[1], r0_plot[1]], y = [r0_plot[2], r0_plot[2]], z = [r0_plot[3], r0_plot[3]], type="scatter3d", name="tag", mode="markers", marker_size=5)

#Plot the Guess
guess = scatter(x = [xyz[1], xyz[1]], y = [xyz[2], xyz[2]], z = [xyz[3], xyz[3]], type="scatter3d", name="guess", mode="markers", marker_size=5)

#Plotting the sphere (Earth)
n = 100
u = range(-π, π; length = n)
v = range(0, π; length = n)
x = cos.(u) * sin.(v)'
y = sin.(u) * sin.(v)' 
z = ones(n) * cos.(v)' 

earth = surface(z=z*6371000, x=x*6371000, y=y*6371000, showscale=false)

plot([sat1,sat3, satellites, tag, earth, guess]) #uncomment to see the plot

data: [
  "scatter3d with fields mode, name, type, x, y, and z",
  "scatter3d with fields mode, name, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z",
  "surface with fields showscale, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z"
]

layout: "layout with fields margin and template"

In [13]:
#Finding the Zenith Angle

function zenith_angle(satposes, r0)
    
    zenithangle = zeros(4)

    #vector between tag and the satellite
    normalvec = r0
    
    for i in 1:4
        
        vector = satposes[i,:] - r0[1:3]
        
        #Find the angle between the normal and the vector going from the tag to the satellte
        theta = acos(dot(normalvec,vector)/(norm(normalvec)*norm(vector))) * (180/pi)
        
        #save zenith angle
        zenithangle[i] = theta
    end
    
    return zenithangle
end

zenith_angle (generic function with 1 method)

In [14]:
#Testing zenith angle function
satposes = [eci_1[1,1] eci_1[2,1] eci_1[3,1];eci_2[1,1] eci_2[2,1] eci_2[3,1];eci_3[1,1] eci_3[2,1] eci_3[3,1];eci_4[1,1] eci_4[2,1] eci_4[3,1]]

zenith_angles = zenith_angle(satposes, r0_plot[1:3])

println(zenith_angles)

#check all angles to see if it is on the horizon 
inhorizon = all(x->x<80, zenith_angles)

[87.71661886808683, 73.7916614769131, 84.30998334955072, 67.55471562049871]


false

In [15]:
#Obtain the orbital elements after each time step (not used in the sim) 
dim = size(t_1)[1]

all_elements = zeros(6,dim)
for i in 1:dim
    
    orbital_elements = sCARTtoOSC(eci_1[:,1], use_degrees=true)
    all_elements[:,i] = orbital_elements
end 

In [16]:
#velocity is the last 3 elements of each column in eci matrices
eci_1[:,1]

6-element Vector{Float64}:
    -6.611755461229845e6
    -1.7473412825817908e6
    -2.3290448551643165e6
 -2336.2081282888425
  -526.900136186714
  7029.342674382558

In [17]:
#Generate TEC Distribution
#mu = 8e16
#sigma = 3e16
#lb = 3e16
#ub = 13e16
#d = Truncated(Normal(mu,sigma), lb, ub)

#f = 1575.42e6 # in 1/s L1 frequency
#f = 400e6 # in 1/s system frequency
h = 350e3 #in meters
#Ip = zeros(4)
#OF = zeros(4)
#Iz = zeros(4)
#Ip_scaled = zeros(4)

350000.0

In [18]:
using ForwardDiff
using BlockDiagonals


#used previously (works for doppler)
###############################################################################################################
# distance_scale = R_EARTH*(1e-3)*1e-4 # scales km to custom scale working

# time_scale = 1/(C_LIGHT/R_EARTH) #scales seconds to custom scale

# velocity_scale = distance_scale/time_scale #scales velocities to custom scale

# frequency_scale = 1e2 #to improve the numerical conditioning of the matrix working

# # #frequency_scale = 1/time_scale #higher conditioning ~70 condition num compared to 15

# c = 10000 #km/s

# ###############################################################################################################
# # working
distance_scale = R_EARTH*(1e-3) # scales km to custom scale working

time_scale = (1/(C_LIGHT/R_EARTH))*1e4 #scales seconds to custom scale

velocity_scale = distance_scale/time_scale #scales velocities to custom scales

frequency_scale = 1

c = 1*1e4 #km/s
###############################################################################################################
# # new units test

# distance_scale = R_EARTH*(1e-3)*1e-2 # scales km to custom scale working

# time_scale = (1/(C_LIGHT/R_EARTH))*1e2 #scales seconds to custom scale

# velocity_scale = distance_scale/time_scale #scales velocities to custom scales

# frequency_scale = 1

# c = 1*1e4 #km/s

10000.0

In [19]:
time_scale

212.75172639599893

In [20]:
#satposet is all the satellite known positions and the measured position
#x is what we want to solve for
#satpose is the satellite position and velocities as well as the measured change in frequency


#pass in zenith angles as z and the corresponding time derivative (finite diff)
function doppler_residual(x, sat_pose_f, time, z, zdot)
    
    omega = OMEGA_EARTH*time_scale #transform to custom scale
    
    #wavelength = 0.7494*1e-3/distance_scale #for a nominal frequency of 400 MHz
    
    omegahat = [0 -omega 0; omega 0 0; 0 0 0]
    
    A1 = [cos(omega*time[1]) sin(omega*time[1]) 0;
          -sin(omega*time[1]) cos(omega*time[1]) 0;
          0 0 1];
    A2 = [cos(omega*time[2]) sin(omega*time[2]) 0;
          -sin(omega*time[2]) cos(omega*time[2]) 0;
          0 0 1];
    A3 = [cos(omega*time[3]) sin(omega*time[3]) 0;
          -sin(omega*time[3]) cos(omega*time[3]) 0;
          0 0 1];
    A4 = [cos(omega*time[4]) sin(omega*time[4]) 0;
          -sin(omega*time[4]) cos(omega*time[4]) 0;
          0 0 1];
    
    #bdot is a velocity. therefore it is scaled
    #Ionosphere Errors at frequency 1
    Idot1 = (((40.3*x[5])*((R_EARTH*sind(z[1]))*(R_EARTH*cosd(z[1])*zdot[1])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[1]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot2 = (((40.3*x[6])*((R_EARTH*sind(z[2]))*(R_EARTH*cosd(z[2])*zdot[2])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[2]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot3 = (((40.3*x[7])*((R_EARTH*sind(z[3]))*(R_EARTH*cosd(z[3])*zdot[3])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[3]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot4 = (((40.3*x[8])*((R_EARTH*sind(z[4]))*(R_EARTH*cosd(z[4])*zdot[4])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[4]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale

    #Ionosphere Errors at frequency 2
    Idot5 = (((40.3*x[5])*((R_EARTH*sind(z[1]))*(R_EARTH*cosd(z[1])*zdot[1])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[1]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot6 = (((40.3*x[6])*((R_EARTH*sind(z[2]))*(R_EARTH*cosd(z[2])*zdot[2])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[2]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot7 = (((40.3*x[7])*((R_EARTH*sind(z[3]))*(R_EARTH*cosd(z[3])*zdot[3])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[3]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot8 = (((40.3*x[8])*((R_EARTH*sind(z[4]))*(R_EARTH*cosd(z[4])*zdot[4])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[4]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    
    
#     #Measurements at frequency 1
#     res1 = (f1/c)*(0.5*(1/norm(x[1:3] - A1*sat_pose_f[1,1:3]))*(-2*x[1:3]'*A1*omegahat*sat_pose_f[1,1:3] - 2*x[1:3]'*A1*sat_pose_f[1,4:6]+sat_pose_f[1,1:3]'*sat_pose_f[1,4:6]+sat_pose_f[1,4:6]'*sat_pose_f[1,1:3]) + Idot1*1e-3/velocity_scale + x[4])- sat_pose_f[1,7]
#     res2 = (f1/c)*(0.5*(1/norm(x[1:3] - A2*sat_pose_f[2,1:3]))*(-2*x[1:3]'*A2*omegahat*sat_pose_f[2,1:3] - 2*x[1:3]'*A2*sat_pose_f[2,4:6]+sat_pose_f[2,1:3]'*sat_pose_f[2,4:6]+sat_pose_f[2,4:6]'*sat_pose_f[2,1:3]) + Idot2*1e-3/velocity_scale + x[4])- sat_pose_f[2,7]
#     res3 = (f1/c)*(0.5*(1/norm(x[1:3] - A3*sat_pose_f[3,1:3]))*(-2*x[1:3]'*A3*omegahat*sat_pose_f[3,1:3] - 2*x[1:3]'*A3*sat_pose_f[3,4:6]+sat_pose_f[3,1:3]'*sat_pose_f[3,4:6]+sat_pose_f[3,4:6]'*sat_pose_f[3,1:3]) + Idot3*1e-3/velocity_scale + x[4])- sat_pose_f[3,7]
#     res4 = (f1/c)*(0.5*(1/norm(x[1:3] - A4*sat_pose_f[4,1:3]))*(-2*x[1:3]'*A4*omegahat*sat_pose_f[4,1:3] - 2*x[1:3]'*A4*sat_pose_f[4,4:6]+sat_pose_f[4,1:3]'*sat_pose_f[4,4:6]+sat_pose_f[4,4:6]'*sat_pose_f[4,1:3]) + Idot4*1e-3/velocity_scale + x[4])- sat_pose_f[4,7]
    
#     #Measurments at frequency 2
#     res5 = (f2/c)*(0.5*(1/norm(x[1:3] - A1*sat_pose_f[1,1:3]))*(-2*x[1:3]'*A1*omegahat*sat_pose_f[1,1:3] - 2*x[1:3]'*A1*sat_pose_f[1,4:6]+sat_pose_f[1,1:3]'*sat_pose_f[1,4:6]+sat_pose_f[1,4:6]'*sat_pose_f[1,1:3]) + Idot5*1e-3/velocity_scale + x[4])- sat_pose_f[5,7]
#     res6 = (f2/c)*(0.5*(1/norm(x[1:3] - A2*sat_pose_f[2,1:3]))*(-2*x[1:3]'*A2*omegahat*sat_pose_f[2,1:3] - 2*x[1:3]'*A2*sat_pose_f[2,4:6]+sat_pose_f[2,1:3]'*sat_pose_f[2,4:6]+sat_pose_f[2,4:6]'*sat_pose_f[2,1:3]) + Idot6*1e-3/velocity_scale + x[4])- sat_pose_f[6,7]
#     res7 = (f2/c)*(0.5*(1/norm(x[1:3] - A3*sat_pose_f[3,1:3]))*(-2*x[1:3]'*A3*omegahat*sat_pose_f[3,1:3] - 2*x[1:3]'*A3*sat_pose_f[3,4:6]+sat_pose_f[3,1:3]'*sat_pose_f[3,4:6]+sat_pose_f[3,4:6]'*sat_pose_f[3,1:3]) + Idot7*1e-3/velocity_scale + x[4])- sat_pose_f[7,7]
#     res8 = (f2/c)*(0.5*(1/norm(x[1:3] - A4*sat_pose_f[4,1:3]))*(-2*x[1:3]'*A4*omegahat*sat_pose_f[4,1:3] - 2*x[1:3]'*A4*sat_pose_f[4,4:6]+sat_pose_f[4,1:3]'*sat_pose_f[4,4:6]+sat_pose_f[4,4:6]'*sat_pose_f[4,1:3]) + Idot8*1e-3/velocity_scale + x[4])- sat_pose_f[8,7]
    
    #Measurments at frequency 1
    res1 = (f1*frequency_scale/c)*(0.5*(1/norm(x[1:3] - A1*sat_pose_f[1,1:3]))*(-2*x[1:3]'*A1*omegahat*sat_pose_f[1,1:3] - 2*x[1:3]'*A1*sat_pose_f[1,4:6]+sat_pose_f[1,1:3]'*sat_pose_f[1,4:6]+sat_pose_f[1,4:6]'*sat_pose_f[1,1:3]) + Idot1 + x[4]) - sat_pose_f[1,7]
    res2 = (f1*frequency_scale/c)*(0.5*(1/norm(x[1:3] - A2*sat_pose_f[2,1:3]))*(-2*x[1:3]'*A2*omegahat*sat_pose_f[2,1:3] - 2*x[1:3]'*A2*sat_pose_f[2,4:6]+sat_pose_f[2,1:3]'*sat_pose_f[2,4:6]+sat_pose_f[2,4:6]'*sat_pose_f[2,1:3]) + Idot2 + x[4]) - sat_pose_f[2,7]
    res3 = (f1*frequency_scale/c)*(0.5*(1/norm(x[1:3] - A3*sat_pose_f[3,1:3]))*(-2*x[1:3]'*A3*omegahat*sat_pose_f[3,1:3] - 2*x[1:3]'*A3*sat_pose_f[3,4:6]+sat_pose_f[3,1:3]'*sat_pose_f[3,4:6]+sat_pose_f[3,4:6]'*sat_pose_f[3,1:3]) + Idot3 + x[4]) - sat_pose_f[3,7]
    res4 = (f1*frequency_scale/c)*(0.5*(1/norm(x[1:3] - A4*sat_pose_f[4,1:3]))*(-2*x[1:3]'*A4*omegahat*sat_pose_f[4,1:3] - 2*x[1:3]'*A4*sat_pose_f[4,4:6]+sat_pose_f[4,1:3]'*sat_pose_f[4,4:6]+sat_pose_f[4,4:6]'*sat_pose_f[4,1:3]) + Idot4 + x[4]) - sat_pose_f[4,7]
    
    #Measurments at frequency 2
    res5 = (f2*frequency_scale/c)*(0.5*(1/norm(x[1:3] - A1*sat_pose_f[1,1:3]))*(-2*x[1:3]'*A1*omegahat*sat_pose_f[1,1:3] - 2*x[1:3]'*A1*sat_pose_f[1,4:6]+sat_pose_f[1,1:3]'*sat_pose_f[1,4:6]+sat_pose_f[1,4:6]'*sat_pose_f[1,1:3]) + Idot5 + x[4]) - sat_pose_f[5,7]
    res6 = (f2*frequency_scale/c)*(0.5*(1/norm(x[1:3] - A2*sat_pose_f[2,1:3]))*(-2*x[1:3]'*A2*omegahat*sat_pose_f[2,1:3] - 2*x[1:3]'*A2*sat_pose_f[2,4:6]+sat_pose_f[2,1:3]'*sat_pose_f[2,4:6]+sat_pose_f[2,4:6]'*sat_pose_f[2,1:3]) + Idot6 + x[4]) - sat_pose_f[6,7]
    res7 = (f2*frequency_scale/c)*(0.5*(1/norm(x[1:3] - A3*sat_pose_f[3,1:3]))*(-2*x[1:3]'*A3*omegahat*sat_pose_f[3,1:3] - 2*x[1:3]'*A3*sat_pose_f[3,4:6]+sat_pose_f[3,1:3]'*sat_pose_f[3,4:6]+sat_pose_f[3,4:6]'*sat_pose_f[3,1:3]) + Idot7 + x[4]) - sat_pose_f[7,7]
    res8 = (f2*frequency_scale/c)*(0.5*(1/norm(x[1:3] - A4*sat_pose_f[4,1:3]))*(-2*x[1:3]'*A4*omegahat*sat_pose_f[4,1:3] - 2*x[1:3]'*A4*sat_pose_f[4,4:6]+sat_pose_f[4,1:3]'*sat_pose_f[4,4:6]+sat_pose_f[4,4:6]'*sat_pose_f[4,1:3]) + Idot8 + x[4]) - sat_pose_f[8,7]

    
    return [res1; res2; res3; res4; res5; res6; res7; res8]
   
end

doppler_residual (generic function with 1 method)

In [21]:
#pose1-4 are satellite locations and velocities
#r0 = [xyz of tag, emmitted frequency]

function measurment(r0, pose1, pose2, pose3, pose4, time, z, zdot)
    
    #Make sure to scale all positions
    
    omega = OMEGA_EARTH*time_scale #change to custom time scale
    
    #wavelength = 0.7494*1e-3/distance_scale #for a nominal frequency of 400 MHz
    
    omegahat = [0 -omega 0; omega 0 0; 0 0 0]
    
     
#     #Ionosphere Errors at frequency 1
#     Idot1 = (((40.3*x[5])*((R_EARTH*sind(z[1]))*(R_EARTH*cosd(z[1])*zdot[1])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[1]))/(R_EARTH+h))^2)^1.5))*1e22
#     Idot2 = (((40.3*x[6])*((R_EARTH*sind(z[2]))*(R_EARTH*cosd(z[2])*zdot[2])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[2]))/(R_EARTH+h))^2)^1.5))*1e22
#     Idot3 = (((40.3*x[7])*((R_EARTH*sind(z[3]))*(R_EARTH*cosd(z[3])*zdot[3])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[3]))/(R_EARTH+h))^2)^1.5))*1e22
#     Idot4 = (((40.3*x[8])*((R_EARTH*sind(z[4]))*(R_EARTH*cosd(z[4])*zdot[4])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[4]))/(R_EARTH+h))^2)^1.5))*1e22

#     #Ionosphere Errors at frequency 1
#     Idot5 = (((40.3*x[5])*((R_EARTH*sind(z[1]))*(R_EARTH*cosd(z[1])*zdot[1])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[1]))/(R_EARTH+h))^2)^1.5))*1e22
#     Idot6 = (((40.3*x[6])*((R_EARTH*sind(z[2]))*(R_EARTH*cosd(z[2])*zdot[2])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[2]))/(R_EARTH+h))^2)^1.5))*1e22
#     Idot7 = (((40.3*x[7])*((R_EARTH*sind(z[3]))*(R_EARTH*cosd(z[3])*zdot[3])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[3]))/(R_EARTH+h))^2)^1.5))*1e22
#     Idot8 = (((40.3*x[8])*((R_EARTH*sind(z[4]))*(R_EARTH*cosd(z[4])*zdot[4])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[4]))/(R_EARTH+h))^2)^1.5))*1e22

    #Ionosphere Errors at frequency 1
    Idot1 = (((40.3*r0[5])*((R_EARTH*sind(z[1]))*(R_EARTH*cosd(z[1])*zdot[1])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[1]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot2 = (((40.3*r0[6])*((R_EARTH*sind(z[2]))*(R_EARTH*cosd(z[2])*zdot[2])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[2]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot3 = (((40.3*r0[7])*((R_EARTH*sind(z[3]))*(R_EARTH*cosd(z[3])*zdot[3])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[3]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot4 = (((40.3*r0[8])*((R_EARTH*sind(z[4]))*(R_EARTH*cosd(z[4])*zdot[4])/(R_EARTH + h)^2))/((f1^2)*(1-((R_EARTH*sind(z[4]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale

    #Ionosphere Errors at frequency 1
    Idot5 = (((40.3*r0[5])*((R_EARTH*sind(z[1]))*(R_EARTH*cosd(z[1])*zdot[1])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[1]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot6 = (((40.3*r0[6])*((R_EARTH*sind(z[2]))*(R_EARTH*cosd(z[2])*zdot[2])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[2]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot7 = (((40.3*r0[7])*((R_EARTH*sind(z[3]))*(R_EARTH*cosd(z[3])*zdot[3])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[3]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale
    Idot8 = (((40.3*r0[8])*((R_EARTH*sind(z[4]))*(R_EARTH*cosd(z[4])*zdot[4])/(R_EARTH + h)^2))/((f2^2)*(1-((R_EARTH*sind(z[4]))/(R_EARTH+h))^2)^1.5))*1e20*1e-3/velocity_scale

    
    A1 = [cos(omega*time[1]) sin(omega*time[1]) 0;
          -sin(omega*time[1]) cos(omega*time[1]) 0;
          0 0 1];
    A2 = [cos(omega*time[2]) sin(omega*time[2]) 0;
          -sin(omega*time[2]) cos(omega*time[2]) 0;
          0 0 1];
    A3 = [cos(omega*time[3]) sin(omega*time[3]) 0;
          -sin(omega*time[3]) cos(omega*time[3]) 0;
          0 0 1];
    A4 = [cos(omega*time[4]) sin(omega*time[4]) 0;
          -sin(omega*time[4]) cos(omega*time[4]) 0;
          0 0 1];
    
    #r0[4] is scaled coming in 
    
    #Measurments at frequency 1
    deltaf1 = (f1*frequency_scale/c)*(0.5*(1/norm(r0[1:3] - A1*pose1[1:3]))*(-2*r0[1:3]'*A1*omegahat*pose1[1:3] - 2*r0[1:3]'*A1*pose1[4:6]+pose1[1:3]'*pose1[4:6]+pose1[4:6]'*pose1[1:3]) + Idot1 + r0[4])
    deltaf2 = (f1*frequency_scale/c)*(0.5*(1/norm(r0[1:3] - A2*pose2[1:3]))*(-2*r0[1:3]'*A2*omegahat*pose2[1:3] - 2*r0[1:3]'*A2*pose2[4:6]+pose2[1:3]'*pose2[4:6]+pose2[4:6]'*pose2[1:3]) + Idot2 + r0[4])
    deltaf3 = (f1*frequency_scale/c)*(0.5*(1/norm(r0[1:3] - A3*pose3[1:3]))*(-2*r0[1:3]'*A3*omegahat*pose3[1:3] - 2*r0[1:3]'*A3*pose3[4:6]+pose3[1:3]'*pose3[4:6]+pose3[4:6]'*pose3[1:3]) + Idot3 + r0[4])
    deltaf4 = (f1*frequency_scale/c)*(0.5*(1/norm(r0[1:3] - A4*pose4[1:3]))*(-2*r0[1:3]'*A4*omegahat*pose4[1:3] - 2*r0[1:3]'*A4*pose4[4:6]+pose4[1:3]'*pose4[4:6]+pose4[4:6]'*pose4[1:3]) + Idot4 + r0[4])
    
    #Measurments at frequency 2
    deltaf5 = (f2*frequency_scale/c)*(0.5*(1/norm(r0[1:3] - A1*pose1[1:3]))*(-2*r0[1:3]'*A1*omegahat*pose1[1:3] - 2*r0[1:3]'*A1*pose1[4:6]+pose1[1:3]'*pose1[4:6]+pose1[4:6]'*pose1[1:3]) + Idot5 + r0[4])
    deltaf6 = (f2*frequency_scale/c)*(0.5*(1/norm(r0[1:3] - A2*pose2[1:3]))*(-2*r0[1:3]'*A2*omegahat*pose2[1:3] - 2*r0[1:3]'*A2*pose2[4:6]+pose2[1:3]'*pose2[4:6]+pose2[4:6]'*pose2[1:3]) + Idot6 + r0[4])
    deltaf7 = (f2*frequency_scale/c)*(0.5*(1/norm(r0[1:3] - A3*pose3[1:3]))*(-2*r0[1:3]'*A3*omegahat*pose3[1:3] - 2*r0[1:3]'*A3*pose3[4:6]+pose3[1:3]'*pose3[4:6]+pose3[4:6]'*pose3[1:3]) + Idot7 + r0[4])
    deltaf8 = (f2*frequency_scale/c)*(0.5*(1/norm(r0[1:3] - A4*pose4[1:3]))*(-2*r0[1:3]'*A4*omegahat*pose4[1:3] - 2*r0[1:3]'*A4*pose4[4:6]+pose4[1:3]'*pose4[4:6]+pose4[4:6]'*pose4[1:3]) + Idot8 + r0[4])

    return [deltaf1, deltaf2, deltaf3, deltaf4, deltaf5, deltaf6, deltaf7, deltaf8]
    
end

measurment (generic function with 1 method)

In [22]:
#Equitorial Position

#In km
x0= x0*1e-3 #x tag position
y0 = y0*1e-3 #y tag position
z0 = z0*1e-3 #z tag position

bdot = 1e4*1e-3 #convert to km/s almost working

#bdot = 1e6*1e-3 #convert to km/s almost working

#bdot = 1*1e-3
TEC1 = 3e-4
TEC2 = 4e-4
TEC3 = 3.5e-4
TEC4 = 4.5e-4

#f0 = 1e6 #nominal frequency

r0_scaled = [x0/distance_scale, y0/distance_scale, z0/distance_scale, bdot/velocity_scale, TEC1, TEC2, TEC3, TEC4]

8-element Vector{Float64}:
 -0.9609082828788089
 -0.24932142011452468
  0.12168918371970193
  0.33356409519815206
  0.0003
  0.0004
  0.00035
  0.00045

In [23]:
#frequency variables
f1 = 400e6 #in Hz
#f2 = 300e6  #in Hz working
#f2 = 430e6 #most recent working



#f2 = 410e6 #working

#works good
f2 = 150e6

#f2 = 500e6

1.5e8

In [24]:
#diff1 = 10e3*1e-3/distance_scale #difference of 10 km
#diff2 = 56e3*1e-3/distance_scale #difference of 10 km
#diff3 = 243e3*1e-3/distance_scale #difference of 10 km

#diff1 = 100e3*1e-3/distance_scale #difference of 10 km
#diff2 = 100e3*1e-3/distance_scale #difference of 10 km
#diff = 100e3*1e-3/distance_scale

#diff = 300e3*1e-3/distance_scale 

#diff = 200e3*1e-3/distance_scale 

#diff = 1e4*1e-3/distance_scale 

#working well for low frequency noise
#diff = 25e3*1e-3/distance_scale 
diff = 50e3*1e-3/distance_scale 

0.007839280574797375

In [25]:
function receiver_pose(all_sats_scaled, guess, zenith_angles, time, zdot) # remember to scale the guess to custom units

    n = 1000 # number of iterations
    #all_r0 = NaN*[zeros(4) for i = 1:n]
    all_r0 = [zeros(8) for i = 1:n] #obtain all the tag positions and frequency offset
    
    sat1poses = zeros(7,n)
    sat2poses = zeros(7,n)
    sat3poses = zeros(7,n)
    sat4poses = zeros(7,n)
    sat5poses = zeros(7,n)
    sat6poses = zeros(7,n)
    sat7poses = zeros(7,n)
    sat8poses = zeros(7,n)

    all_sats_noise = zeros(8,4)

    iters = 0

     #Monte Carlo Simulation
    for i in 1:n

        #Parameters for line search
        #b = 0.01 works
        b = 0.1
        c=0.5
        β = 1.0
        α = 1
#########################################################################################################333        
        #previous noise
        #create noise from normal distribution
        #scaled to the variable (0.1m error for distance & 1e-11 for time)
        #gpsnoise = randn(12)*(0.1*1e-3/distance_scale) #0.1 m switch to km then to custom scale
        #velocitynoise = randn(12)*(0.1*1e-3/velocity_scale)# 0.1 m/s
        #doppler_noise = randn(8)* 1e-4/frequency_scale #0.001 ~ 500's of error
############################################################################################################
#         # noise testing (working!)
#         gpsnoise = randn(12)*(0.001*1e-3/distance_scale) #0.1 m switch to km then to custom scale
#         velocitynoise = randn(12)*(0.001*1e-3/velocity_scale)# 0.1 m/s
#         doppler_noise = randn(8)* 1e-3/frequency_scale #0.001 ~ 300 of error
###########################################################################################################        
        # new noise testing 
        #gpsnoise = randn(12)*(0.1*1e-3/distance_scale) #0.1 m switch to km then to custom scale
        #velocitynoise = randn(12)*(0.1*1e-3/velocity_scale)# 0.1 m/s
        #doppler_noise = randn(8)* 1e-1/frequency_scale #0.001 ~ 3000's of error
        
        # noise testing (working!)
        gpsnoise = randn(12)*(0.1*1e-3/distance_scale) #0.1 m switch to km then to custom scale
        velocitynoise = randn(12)*(0.01*1e-3/velocity_scale)# 0.1 m/s
        doppler_noise = randn(8)*1/frequency_scale #transmission time ~ 1 second
        
        #TEC = rand(d,4) #vTEC for each satellite from custom distribution
        
        #Calculating random TEC time delay
#         for i=1:4
        
#             OF[i] = (1-((R_EARTH*sind(zenith_angles[i]))/(R_EARTH+hi))^2)^(-1/2) #normal units (m and s)
#             Ip[i] = ((40.3*TEC[i])/(f^2))*OF[i] * 1e-3 #scale to km to use the custom unit
#             Ip_scaled[i] = Ip[i]/distance_scale #scale to custom units
        
#         end
        
        sat1_noise = [all_sats_scaled[1,1]+gpsnoise[1],all_sats_scaled[1,2] + gpsnoise[2],all_sats_scaled[1,3]+gpsnoise[3], all_sats_scaled[1,4]+velocitynoise[1], all_sats_scaled[1,5]+velocitynoise[2],all_sats_scaled[1,6]+velocitynoise[3], all_sats_scaled[1,7] + doppler_noise[1]]
        sat2_noise =[all_sats_scaled[2,1]+gpsnoise[4],all_sats_scaled[2,2] + gpsnoise[5],all_sats_scaled[2,3]+gpsnoise[6], all_sats_scaled[2,4]+velocitynoise[4], all_sats_scaled[2,5]+velocitynoise[5],all_sats_scaled[2,6]+velocitynoise[6], all_sats_scaled[2,7] + doppler_noise[2]]
        sat3_noise = [all_sats_scaled[3,1]+gpsnoise[7],all_sats_scaled[3,2] + gpsnoise[8],all_sats_scaled[3,3]+gpsnoise[9], all_sats_scaled[3,4]+velocitynoise[7], all_sats_scaled[3,5]+velocitynoise[8],all_sats_scaled[3,6]+velocitynoise[9], all_sats_scaled[3,7] + doppler_noise[3]]
        sat4_noise = [all_sats_scaled[4,1]+gpsnoise[10],all_sats_scaled[4,2] + gpsnoise[11],all_sats_scaled[4,3]+gpsnoise[12], all_sats_scaled[4,4]+velocitynoise[10], all_sats_scaled[4,5]+velocitynoise[11],all_sats_scaled[4,6]+velocitynoise[12], all_sats_scaled[4,7] + doppler_noise[4]]
        
        sat5_noise = [all_sats_scaled[1,1]+gpsnoise[1],all_sats_scaled[1,2] + gpsnoise[2],all_sats_scaled[1,3]+gpsnoise[3], all_sats_scaled[1,4]+velocitynoise[1], all_sats_scaled[1,5]+velocitynoise[2],all_sats_scaled[1,6]+velocitynoise[3], all_sats_scaled[5,7] + doppler_noise[5]]
        sat6_noise =[all_sats_scaled[2,1]+gpsnoise[4],all_sats_scaled[2,2] + gpsnoise[5],all_sats_scaled[2,3]+gpsnoise[6], all_sats_scaled[2,4]+velocitynoise[4], all_sats_scaled[2,5]+velocitynoise[5],all_sats_scaled[2,6]+velocitynoise[6], all_sats_scaled[6,7] + doppler_noise[6]]
        sat7_noise = [all_sats_scaled[3,1]+gpsnoise[7],all_sats_scaled[3,2] + gpsnoise[8],all_sats_scaled[3,3]+gpsnoise[9], all_sats_scaled[3,4]+velocitynoise[7], all_sats_scaled[3,5]+velocitynoise[8],all_sats_scaled[3,6]+velocitynoise[9], all_sats_scaled[7,7] + doppler_noise[7]]
        sat8_noise = [all_sats_scaled[4,1]+gpsnoise[10],all_sats_scaled[4,2] + gpsnoise[11],all_sats_scaled[4,3]+gpsnoise[12], all_sats_scaled[4,4]+velocitynoise[10], all_sats_scaled[4,5]+velocitynoise[11],all_sats_scaled[4,6]+velocitynoise[12], all_sats_scaled[8,7] + doppler_noise[8]]

        all_sats_noise = vcat(sat1_noise',sat2_noise',sat3_noise',sat4_noise', sat5_noise',sat6_noise',sat7_noise',sat8_noise')
        
        
        #println("allsats noise size: ", size(all_sats_noise))
        sat1poses[:,i] = sat1_noise
        sat2poses[:,i] = sat2_noise
        sat3poses[:,i] = sat3_noise
        sat4poses[:,i] = sat4_noise
        
        sat5poses[:,i] = sat5_noise
        sat6poses[:,i] = sat6_noise
        sat7poses[:,i] = sat7_noise
        sat8poses[:,i] = sat8_noise
        
        X = NaN*[zeros(8) for i = 1:n]
        R = NaN*[zeros(8) for i = 1:n]
        
        #Centroid guess
        #X[1] = [guess[1]/distance_scale, guess[2]/distance_scale, guess[3]/distance_scale, 1.002*1e4*1e-3/velocity_scale, 3.1e-4, 4.2e-4, 3.2e-4, 4.7e-4]
        #works
        #X[1] = [guess[1]/distance_scale + diff, guess[2]/distance_scale + diff, guess[3]/distance_scale + diff, 1.002*1e4*1e-3/velocity_scale, 3.1e-4, 4.2e-4, 3.2e-4, 4.7e-4]
        X[1] = [r0_scaled[1]+diff, r0_scaled[2]+diff, r0_scaled[3]+diff, 1.002*1e4*1e-3/velocity_scale, 3.1e-4, 4.2e-4, 3.2e-4, 4.7e-4]
        #X[1] = r0_scaled
        #println("my guess: ", myguess )
        #println("intial guess: ", X[1])
        #Initial residual
        R[1] = doppler_residual(X[1], all_sats_noise, time, zenith_angles, zdot)
        
        #println("initial residual: ", R[1])
        iters = 0

        for k=1:1000
            R[k] = doppler_residual(X[k], all_sats_noise, time, zenith_angles, zdot) #calculate residual
            
            #println("residual: ", R[k])
            #println("residual norm: ", norm(R[k]))

            iters += 1

            if(norm(R[k]) < 1e-6)
                
            #if(norm(R[k]) < 1)
                
                #println("this is converged solution: ", X[k])
                
                break

            end
            #println("type of all sats noise: ", typeof(all_sats_noise))
            
            #println("ALL SATS NOISE: ", all_sats_noise)

            jacobian = ForwardDiff.jacobian(dx -> doppler_residual(dx, all_sats_noise, time, zenith_angles, zdot), X[k])
            
            if rank(jacobian) != 8
                break
            end
            
            conditionnum = cond(jacobian)
            
            #println("this is R[k]: ", R[k])
            #println("this is the condition number: ", conditionnum)
            
            #println("this is the jacobian: ", jacobian)

            deltax = (jacobian)\-R[k]
            
            #println("R[k]: ", R[k])
            
            #println("this is delta x: ", deltax)
            
            #println("this is x[k]: ", X[k])
            
            if iters > 50
                break
            end
            
            while norm(doppler_residual(X[k] + α*deltax, all_sats_noise, time, zenith_angles, zdot)) > norm(doppler_residual(X[k], all_sats_noise, time, zenith_angles, zdot) + b*α*jacobian'*deltax)
                α = c*α
                
                #print("this is alpha: ", α)
                
            end

            X[k+1] = X[k] + α*deltax
             
        end  
        
        R = R[1:iters]
        X = X[1:iters]

        all_r0[i] = X[end]

    end
    x_values = zeros(n)
    y_values = zeros(n)
    z_values = zeros(n)

    for j in 1:n

        x_values[j] = all_r0[j][1]
        y_values[j] = all_r0[j][2]
        z_values[j] = all_r0[j][3]

    end
    
    #mean calculation
    mean = sum(all_r0, dims = 1)/ n
    mean = mean[1]
    mean_rescaled = [mean[1:3]*distance_scale*1e3; mean[4]*1e3*velocity_scale; mean[5:8]] # in meters
    
    return mean_rescaled, all_r0, iters
end

receiver_pose (generic function with 1 method)

In [26]:
#Navigation
#count = 0
n=1000
PDOP_array = zeros(size(eci_1)[2],1)
for i=1:size(eci_1)[2] - 1
    
    satposes = [eci_1[1,i] eci_1[2,i] eci_1[3,i];eci_2[1,i] eci_2[2,i] eci_2[3,i];eci_3[1,i] eci_3[2,i] eci_3[3,i];eci_4[1,i] eci_4[2,i] eci_4[3,i]]
    satposes2 = [eci_1[1,i+1] eci_1[2,i+1] eci_1[3,i+1];eci_2[1,i+1] eci_2[2,i+1] eci_2[3,i+1];eci_3[1,i+1] eci_3[2,i+1] eci_3[3,i+1];eci_4[1,i+1] eci_4[2,i+1] eci_4[3,i+1]]
    zenith_angles = zenith_angle(satposes, r0_plot[1:3])
    zenith_angles2 = zenith_angle(satposes2, r0_plot[1:3])
    
    zdot = zenith_angles - zenith_angles2
    
    #println(zenith_angles)

    #check all angles to see if it is on the horizon 
    
    inhorizon = all(x->x<70, zenith_angles)
    
    if inhorizon==false
        
        continue #skip the current iteration
    end

    #In km then to custom units
    r1 = [eci_1[1,i], eci_1[2,i], eci_1[3,i]]*1e-3/distance_scale
    r2 = [eci_2[1,i], eci_2[2,i], eci_2[3,i]]*1e-3/distance_scale
    r3 = [eci_3[1,i], eci_3[2,i], eci_3[3,i]]*1e-3/distance_scale
    r4 = [eci_4[1,i], eci_4[2,i], eci_4[3,i]]*1e-3/distance_scale
    
    v1 = [eci_1[4,i], eci_1[5,i], eci_1[6,i]]*1e-3/velocity_scale
    v2 = [eci_2[4,i], eci_2[5,i], eci_2[6,i]]*1e-3/velocity_scale
    v3 = [eci_3[4,i], eci_3[5,i], eci_3[6,i]]*1e-3/velocity_scale
    v4 = [eci_4[4,i], eci_4[5,i], eci_4[6,i]]*1e-3/velocity_scale

    pose1 = [r1' v1']
    pose2 = [r2' v2']
    pose3 = [r3' v3']
    pose4 = [r4' v4']
    
    #at second frequency
    pose5= [r1' v1']
    pose6= [r2' v2']
    pose7= [r3' v3']
    pose8= [r4' v4']
    
    time = [0.006, 0.006, 0.006, 0.008]/time_scale # assume a fixed time for the rotation matrix
    
    #calculate the rdots. need to build the pose matrices
    deltaf = measurment(r0_scaled, pose1, pose2, pose3, pose4, time, zenith_angles, zdot)
    
    pose1_rdot1 = [pose1 deltaf[1]]
    pose2_rdot2 = [pose2 deltaf[2]]
    pose3_rdot3 = [pose3 deltaf[3]]
    pose4_rdot4 = [pose4 deltaf[4]]
    
    pose5_rdot5= [pose1 deltaf[5]]
    pose6_rdot6= [pose2 deltaf[6]]
    pose7_rdot7= [pose3 deltaf[7]]
    pose8_rdot8= [pose4 deltaf[8]]
    
    #println("this is deltaf: ", deltaf)
    
    all_sats_scaled = vcat(pose1_rdot1,pose2_rdot2,pose3_rdot3,pose4_rdot4, pose5_rdot5,pose6_rdot6,pose7_rdot7,pose8_rdot8)

#   #Generate a guess at the centroid of all 4 sats on the surface of the Earth. Scaled to km
    centroid_guess = [(eci_1[1,i]+eci_2[1,i]+eci_3[1,i]+eci_4[1,i])/4, (eci_1[2,i]+eci_2[2,i]+eci_3[2,i]+eci_4[2,i])/4, (eci_1[3,i]+eci_2[3,i]+eci_3[3,i]+eci_4[3,i])/4] 
    onearth = sECEFtoGEOC(centroid_guess, use_degrees = true)
    geodetic = [onearth[1], onearth[2], 0]

    xyz_guess = sGEOCtoECEF(geodetic, use_degrees = true)*1e-3 #change to km

    #xyz_guess = [eci_2[1,i], eci_2[2,i], eci_2[3,i]]*1e-3
    
    #println("this is the guess: ", xyz_guess)
    #xyz_guess
    
    #Find all possible positions from montecarlo and send unscaled guess
    mean_rescaled, all_r0, iters = receiver_pose(all_sats_scaled, xyz_guess, zenith_angles, time, zdot)
    
    all_r0_scaled = zeros(n,8)

    #Rescale back to units (m and s)
    for i in 1:n
    
        all_r0_scaled[i,:] = [all_r0[i][1:3]*distance_scale*1e3; all_r0[i][4]*1e3*velocity_scale; all_r0[i][5:8]]
        
    end
    
    totalsum = zeros(8,8)

    for i in 1:n
        
        value = all_r0_scaled[i,:] - mean_rescaled
        matrixvalue = value*transpose(value)
        totalsum += matrixvalue
    
    end
    
    covariancematrix = totalsum/n
    
    PDOP = sqrt(covariancematrix[1,1] + covariancematrix[2,2] + covariancematrix[3,3])
    PDOP_array[i,1] = PDOP
    println("cov position erors: ", PDOP)
    println("Mean (m): ", mean_rescaled)
    println("Iterations: ", iters)
    println("Time step: ", i )

end    

cov position erors: 3743.6398194469743
Mean (m): [-6.128793114171892e6, -1.590285346776797e6, 776144.4166865862, 10000.021276136218, 0.0002995160319143503, 0.00039998983516620275, 0.00035092671832899117, 0.0004489908031062258]
Iterations: 5
Time step: 203
cov position erors: 3772.2283902538297
Mean (m): [-6.128865385533204e6, -1.5901057923018704e6, 776157.509939487, 10000.030710530511, 0.0002985599003645719, 0.000402874077883683, 0.0003498623018404414, 0.0004400918767678093]
Iterations: 5
Time step: 204
cov position erors: 3681.4990302216543
Mean (m): [-6.128812828299804e6, -1.5901826757568992e6, 776152.0782832098, 10000.010281282795, 0.0003017379065208558, 0.0003977625950367783, 0.0003493259598793141, 0.00044148433489471246]
Iterations: 5
Time step: 205
cov position erors: 3746.493837763201
Mean (m): [-6.128817209132456e6, -1.5902264223097963e6, 776148.4168543508, 10000.027506677608, 0.0002998915410997596, 0.00040261195893923903, 0.0003501141642961497, 0.0004350276036901642]
Iteration

cov position erors: 3572.0989862034926
Mean (m): [-6.128758844405918e6, -1.5903530787350803e6, 776144.1648456014, 10000.012997658074, 0.0002994520585738377, 0.0003993714760412718, 0.0003522694397151061, 0.00045443646285324814]
Iterations: 5
Time step: 236
cov position erors: 3556.84124997803
Mean (m): [-6.128816678464221e6, -1.5901686948457372e6, 776147.595858734, 9999.944845451524, 0.00030202515825694155, 0.0004053391520970167, 0.0003504257932699754, 0.0004471530779698754]
Iterations: 5
Time step: 237
cov position erors: 3570.5000772930725
Mean (m): [-6.128785094802784e6, -1.5902696848596076e6, 776157.1679739663, 10000.056575378649, 0.00029706897199372183, 0.00040030728794064526, 0.00035060685445334336, 0.0004450597757153986]
Iterations: 5
Time step: 238
cov position erors: 3503.505617198555
Mean (m): [-6.128762271946243e6, -1.5903078499756064e6, 776138.8163053292, 9999.938667255688, 0.0003006133732705062, 0.0003985305461378874, 0.0003517149954743379, 0.00044279784241946]
Iterations: 

cov position erors: 4120.501173449294
Mean (m): [-6.128731546883985e6, -1.5904416373726637e6, 776149.9407131654, 10000.096076067406, 0.0002984446383379157, -0.0008764526775246325, 0.0003505850230929148, 0.00045156306317509914]
Iterations: 5
Time step: 269
cov position erors: 4227.118707877361
Mean (m): [-6.12877276031434e6, -1.5902910730180051e6, 776130.8530100443, 9999.931117584942, 0.0003004077893872494, 0.000418950062301294, 0.0003493038023548815, 0.00044781782540447116]
Iterations: 5
Time step: 270
cov position erors: 4062.726952673686
Mean (m): [-6.128797392023809e6, -1.5902275060757883e6, 776140.6724925055, 9999.954793392504, 0.0003003309580880427, 0.000495280768340094, 0.000349558905638227, 0.000446438605853825]
Iterations: 5
Time step: 271
cov position erors: 4293.055652547392
Mean (m): [-6.128870675770252e6, -1.5900370746844949e6, 776161.070378377, 9999.961611307546, 0.00030048472297141955, 0.0003915080363651984, 0.0003482376195244687, 0.0004485855532499623]
Iterations: 5
Time

cov position erors: 7885.778283270135
Mean (m): [-6.128837384850709e6, -1.5902221955985439e6, 776155.8228460283, 10000.019736353064, 0.00029981594377502, 0.0003964510405369034, 0.00035176622131995216, 0.0004514757695127978]
Iterations: 5
Time step: 302
cov position erors: 8304.51749068247
Mean (m): [-6.128669573175408e6, -1.5906787934091275e6, 776060.9981667341, 9999.78049759721, 0.0003000837600414886, 0.0004061635230737737, 0.00035232198717163914, 0.00045137718238040444]
Iterations: 5
Time step: 303
cov position erors: 8496.503221816056
Mean (m): [-6.128787982106623e6, -1.5903644452293792e6, 776133.0052054207, 9999.947691089017, 0.0002993266484177184, 0.00039663920210363744, 0.000351607187343943, 0.00044998131664742623]
Iterations: 5
Time step: 304
cov position erors: 8597.273533337253
Mean (m): [-6.128890380943315e6, -1.5900716210509306e6, 776174.464364671, 10000.015987188055, 0.00030108886583714485, 0.00039870930303245673, 0.0003500490248973849, 0.000449867080580334]
Iterations: 6
T

cov position erors: 242297.771694831
Mean (m): [-6.237554738519745e6, -1.4011069623838072e6, 820354.2576211934, 10089.65893671934, 0.00030101621167168596, 0.00040054182892308547, 0.0003529230780498263, 0.000450432503970433]
Iterations: 6
Time step: 334
cov position erors: 97549.53940508595
Mean (m): [-6.116630220944771e6, -1.569648816093055e6, 793239.4936920863, 10004.781728748307, 0.0002989050972960323, 0.00041291440737786604, 0.00034731504317453286, 0.0004549505519227382]
Iterations: 51
Time step: 335
cov position erors: 18725.65085812711
Mean (m): [-6.1290963958503725e6, -1.589800407044137e6, 776261.7282546344, 10000.263166730581, 0.0002971299499530589, 0.00039986858331991716, 0.00035045737202652486, 0.0004499627892342798]
Iterations: 33
Time step: 336
cov position erors: 17642.304080662278
Mean (m): [-6.129308024549634e6, -1.5890016197327764e6, 776407.6206782468, 10000.585551946591, 0.00029977579436178686, 0.0004017803277274372, 0.0003542123917347227, 0.0004506349137418801]
Iterati

cov position erors: 5045.964717151745
Mean (m): [-6.128793895224243e6, -1.5903503922762317e6, 776132.80215513, 9999.943768780073, 0.0003017592011194919, 0.0003999708724442135, 0.00035145756953583793, 0.0004491614085764814]
Iterations: 6
Time step: 367
cov position erors: 4764.918148376819
Mean (m): [-6.128861572465909e6, -1.589990487227412e6, 776174.2821047183, 10000.042694728494, 0.0003003164661476533, 0.00039824634493053904, 0.00033769958481938845, 0.00044766131948264707]
Iterations: 5
Time step: 368
cov position erors: 4970.371980158183
Mean (m): [-6.128834324253432e6, -1.5901502455451516e6, 776150.4741593655, 9999.969886467747, 0.00030076207452031607, 0.00040005678522862673, 0.0003518266005538558, 0.00044999238968282716]
Iterations: 5
Time step: 369
cov position erors: 4832.5275810270505
Mean (m): [-6.128857828225571e6, -1.5900304286132806e6, 776164.914626975, 10000.018170874906, 0.00029698951141399877, 0.0004015020310094405, 0.0003523027747427998, 0.0004494656547971841]
Iterations

cov position erors: 3635.4487908306683
Mean (m): [-6.128828688983713e6, -1.5901634945064965e6, 776153.1226087536, 9999.992590758513, 0.00029967486342649116, 0.00040027848960505426, 0.00036415755571839967, 0.0004494126562483838]
Iterations: 5
Time step: 400
cov position erors: 3486.4026763034876
Mean (m): [-6.128800992908404e6, -1.5902499254809197e6, 776146.2654732617, 9999.982455367292, 0.0002965874246556029, 0.0003994228994071824, 0.00036212641858012916, 0.0004496310409701788]
Iterations: 5
Time step: 401
cov position erors: 3403.918332003136
Mean (m): [-6.128757489100695e6, -1.5903968682695604e6, 776146.5213720684, 10000.046579224785, 0.0003007241978008354, 0.00040037983979281875, 0.00036101590079174936, 0.0004510745433424229]
Iterations: 5
Time step: 402
cov position erors: 3494.680258985867
Mean (m): [-6.128791022360924e6, -1.590299865948391e6, 776155.0140113595, 10000.016422676004, 0.00030560940802442315, 0.0004010485933217385, 0.0003505638652605855, 0.0004516999159103663]
Iterati

cov position erors: 3475.8800617421066
Mean (m): [-6.1288476696191775e6, -1.5901333925255358e6, 776149.5613917994, 9999.945258824753, 0.00030264321378259656, 0.0004016129530839808, 0.00035235486766123836, 0.0004509868046966289]
Iterations: 5
Time step: 433
cov position erors: 3369.965793043463
Mean (m): [-6.128920349402825e6, -1.5899638948114526e6, 776146.7774313993, 9999.804123170792, 0.00030163419047106005, 0.00040060506464651807, 0.0003554752819287468, 0.00044798627023318364]
Iterations: 5
Time step: 434
cov position erors: 3280.538037748792
Mean (m): [-6.128777905331778e6, -1.590218378269683e6, 776153.9668332037, 10000.094078677956, 0.0002969608763235522, 0.00039963790158259986, 0.00034825182989707743, 0.0004501643134260106]
Iterations: 5
Time step: 435
cov position erors: 3270.972644348444
Mean (m): [-6.128828027025707e6, -1.5901727753082982e6, 776151.1400237216, 9999.970580662133, 0.0003614887914297847, 0.0004015915845942131, 0.00034974646316555404, 0.0004493058903951738]
Iterati

In [27]:
final_PDOP = PDOP_array[PDOP_array .!=0]

PDOP_max = findmax(final_PDOP)[1]
PDOP_min = findmin(final_PDOP)[1]

println("Maximum PDOP: ", PDOP_max)
println("Minimum PDOP: ", PDOP_min)

Maximum PDOP: 7.154404491929036e13
Minimum PDOP: 3234.6792889811386


In [341]:
tag =[-6.128804e6, -1.590206e6, 776.1502e3]

3-element Vector{Float64}:
     -6.128804e6
     -1.590206e6
 776150.2

In [681]:
initialguess = [-0.9625008623511324, -0.2580926606494148, 0.08354931473148393, 0.40027691423778244, 0.00031, 0.00042, 0.00032, 0.00047]

8-element Vector{Float64}:
 -0.9625008623511324
 -0.2580926606494148
  0.08354931473148393
  0.40027691423778244
  0.00031
  0.00042
  0.00032
  0.00047

In [650]:
r0_scaled

8-element Vector{Float64}:
 -0.9609082828788089
 -0.24932142011452468
  0.12168918371970193
  0.33356409519815206
  0.0003
  0.0004
  0.00035
  0.00045

In [ ]:
change = r0_scaled - initialguess

In [ ]:
change[1:3]*1e3*distance_scale

In [ ]:
bdot = 1e-6
TEC1 = 3e-6
TEC2 = 4e-6
TEC3 = 3.5e-6
TEC4 = 4.2e-6

actualpose =[-6.128804e6, -1.590206e6, 776.1502e3, bdot, TEC1, TEC2, TEC3, TEC4]

In [ ]:
i=303

satposes = [eci_1[1,i] eci_1[2,i] eci_1[3,i];eci_2[1,i] eci_2[2,i] eci_2[3,i];eci_3[1,i] eci_3[2,i] eci_3[3,i];eci_4[1,i] eci_4[2,i] eci_4[3,i]]
satposes2 = [eci_1[1,i+1] eci_1[2,i+1] eci_1[3,i+1];eci_2[1,i+1] eci_2[2,i+1] eci_2[3,i+1];eci_3[1,i+1] eci_3[2,i+1] eci_3[3,i+1];eci_4[1,i+1] eci_4[2,i+1] eci_4[3,i+1]]
zenith_angles = zenith_angle(satposes, r0_plot[1:3])
zenith_angles2 = zenith_angle(satposes2, r0_plot[1:3])

println("satposes: ", satposes)

println("satposes2: ", satposes2)
    
zdot = zenith_angles - zenith_angles2

#check all angles to see if it is on the horizon 
    
inhorizon = all(x->x<70, zenith_angles)
    
#if inhorizon==false
#    continue #skip the current iteration
#end

#In km then to custom units
r1 = [eci_1[1,i], eci_1[2,i], eci_1[3,i]]*1e-3/distance_scale
r2 = [eci_2[1,i], eci_2[2,i], eci_2[3,i]]*1e-3/distance_scale
r3 = [eci_3[1,i], eci_3[2,i], eci_3[3,i]]*1e-3/distance_scale
r4 = [eci_4[1,i], eci_4[2,i], eci_4[3,i]]*1e-3/distance_scale
    
v1 = [eci_1[4,i], eci_1[5,i], eci_1[6,i]]*1e-3/velocity_scale
v2 = [eci_2[4,i], eci_2[5,i], eci_2[6,i]]*1e-3/velocity_scale
v3 = [eci_3[4,i], eci_3[5,i], eci_3[6,i]]*1e-3/velocity_scale
v4 = [eci_4[4,i], eci_4[5,i], eci_4[6,i]]*1e-3/velocity_scale

pose1 = [r1' v1']
pose2 = [r2' v2']
pose3 = [r3' v3']
pose4 = [r4' v4']
    
#at second frequency
pose5= [r1' v1']
pose6= [r2' v2']
pose7= [r3' v3']
pose8= [r4' v4']
    
time = [0.006, 0.006, 0.006, 0.008]/time_scale # assume a fixed time for the rotation matrix
    
#calculate the rdots. need to build the pose matrices
deltaf = measurment(r0_scaled, pose1, pose2, pose3, pose4, time, zenith_angles, zdot)
    
pose1_rdot1 = [pose1 deltaf[1]]
pose2_rdot2 = [pose2 deltaf[2]]
pose3_rdot3 = [pose3 deltaf[3]]
pose4_rdot4 = [pose4 deltaf[4]]
    
pose5_rdot5= [pose1 deltaf[5]]
pose6_rdot6= [pose2 deltaf[6]]
pose7_rdot7= [pose3 deltaf[7]]
pose8_rdot8= [pose4 deltaf[8]]
    
all_sats_scaled = vcat(pose1_rdot1, pose2_rdot2, pose3_rdot3, pose4_rdot4, pose5_rdot5, pose6_rdot6, pose7_rdot7, pose8_rdot8)
    
println("this is deltaf: ", deltaf)

In [ ]:
R = doppler_residual(initialguess, all_sats_scaled, time, zenith_angles, zdot)

In [ ]:
jacobian = ForwardDiff.jacobian(dx -> doppler_residual(dx, all_sats_scaled, time, zenith_angles, zdot), r0_scaled)

In [ ]:
println(zdot)

In [ ]:
1e-3/velocity_scale

In [ ]:
f1*frequency_scale/c

In [ ]:
f2*frequency_scale/c

In [ ]:
velocity_scale

In [ ]:
2800.1524487715533*f1*frequency_scale/c

In [ ]:
 1.2e6*1e-3/velocity_scale

In [ ]:
1e4*1e-3/velocity_scale

In [ ]:
8.680472591191815e-5*velocity_scale*1e3

In [175]:
#For Testing
j = 323

centroid_guess = [(eci_1[1,j]+eci_2[1,j]+eci_3[1,j]+eci_4[1,j])/4, (eci_1[2,j]+eci_2[2,j]+eci_3[2,j]+eci_4[2,j])/4, (eci_1[3,j]+eci_2[3,j]+eci_3[3,j]+eci_4[3,j])/4] 
onearth = sECEFtoGEOC(centroid_guess, use_degrees = true)
geodetic = [onearth[1], onearth[2], 0]

#Guess
xyz = sGEOCtoECEF(geodetic, use_degrees = true)

3-element Vector{Float64}:
     -6.148534936549531e6
     -1.6529039596373022e6
 379550.0296590537

In [176]:
#Testing zenith angle function
satposes = [eci_1[1,j] eci_1[2,j] eci_1[3,j];eci_2[1,j] eci_2[2,j] eci_2[3,j];eci_3[1,j] eci_3[2,j] eci_3[3,j];eci_4[1,j] eci_4[2,j] eci_4[3,j]]

zenith_angles = zenith_angle(satposes, r0_plot[1:3])

println(zenith_angles)

#check all angles to see if it is on the horizon 
inhorizon = all(x->x<70, zenith_angles)

[59.85279054618235, 0.7535135682965504, 48.74064880913165, 24.79600620394988]


true

In [178]:
plotdiff = 25e3
#plotdiffz = 50e3
#Plot Satellite 1 and 2 Orbit
sat1 = scatter(x=eci_1[1,:], y=eci_1[2,:], z=eci_1[3,:], type="scatter3d", mode="lines", name="orbit 1&2")

#Plot Satellite 3 and 4 Orbit
sat3 = scatter(x=eci_3[1,:], y=eci_3[2,:], z=eci_3[3,:], type="scatter3d", mode="lines", name="orbit 3&4")

#Plot all 4 satellite initial positions
satellites = scatter(x=[eci_1[1,j],eci_2[1,j], eci_3[1,j], eci_4[1,j]], y=[eci_1[2,j],eci_2[2,j], eci_3[2,j], eci_4[2,j]],z=[eci_1[3,j],eci_2[3,j], eci_3[3,j], eci_4[3,j]], mode="markers", marker_size = 4, type="scatter3d", name="satellites")

#Plot Tag position
tag = scatter(x = [r0_plot[1], r0_plot[1]], y = [r0_plot[2], r0_plot[2]], z = [r0_plot[3], r0_plot[3]], type="scatter3d", name="tag", mode="markers", marker_size=5)

#Plot the Guess
guess = scatter(x = [xyz[1], xyz[1]], y = [xyz[2], xyz[2]], z = [xyz[3], xyz[3]], type="scatter3d", name="guess", mode="markers", marker_size=5)

guess_moved = scatter(x = [xyz[1]+diff, xyz[1]+diff], y = [xyz[2]+diff, xyz[2]+diff], z = [xyz[3]+diff, xyz[3]+diff], type="scatter3d", name="guess moved", mode="markers", marker_size=5)

#Plotting the sphere (Earth)
n = 100
u = range(-π, π; length = n)
v = range(0, π; length = n)
x = cos.(u) * sin.(v)'
y = sin.(u) * sin.(v)' 
z = ones(n) * cos.(v)' 

earth = surface(z=z*6371000, x=x*6371000, y=y*6371000, showscale = false)

plot([sat1,sat3, satellites, tag, earth, guess, guess_moved]) #uncomment to see the plot

data: [
  "scatter3d with fields mode, name, type, x, y, and z",
  "scatter3d with fields mode, name, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z",
  "surface with fields showscale, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z",
  "scatter3d with fields marker, mode, name, type, x, y, and z"
]

layout: "layout with fields margin and template"

In [171]:
eci_1[:,355]

6-element Vector{Float64}:
     -6.987487769372123e6
     -1.815301934558241e6
 257339.50092052715
    236.99408591290472
    147.21083040063195
   7421.328252694564

In [598]:
initialguess = [-0.9593404267638495, -0.2405414258707516, 0.15978808731321717, 0.3342312233885483, 0.00031, 0.00042, 0.00032, 0.00047]
myguess = [-0.9625008623511324, -0.2580926606494148, 0.08354931473148393, 0.3342312233885483, 0.00031, 0.00042, 0.00032, 0.00047]

8-element Vector{Float64}:
 -0.9625008623511324
 -0.2580926606494148
  0.08354931473148393
  0.3342312233885483
  0.00031
  0.00042
  0.00032
  0.00047

In [655]:
xyz_moved = [xyz[1] + plotdiff, xyz[2] + plotdiff, xyz[3] + plotdiff]

good_guess = [r0_plot[1] + plotdiff, r0_plot[2] + plotdiff,r0_plot[3] - plotdiff]

3-element Vector{Float64}:
     -6.028804e6
     -1.490206e6
 676150.2

In [600]:
difference = r0_plot[1:3] - xyz_moved

3-element Vector{Float64}:
 -45599.32229582034
   6022.246198171517
 130864.94604534365

In [656]:
difference2 = r0_plot[1:3] - good_guess

3-element Vector{Float64}:
 -100000.0
 -100000.0
  100000.0

In [541]:
sum(difference)

-293041.48682861007

In [542]:
norm(difference)

241039.32975068036

In [ ]:
diff1 = initialguess-r0_scaled

In [ ]:
diff2 = myguess-r0_scaled

In [ ]:
norm(diff1)

In [ ]:
norm(diff2)